In [1]:
!pip install nglview --user # Устанавливаю внешний пакет, позволяющий визуализировать структуру биомолекул.

/usr/lib/python3/dist-packages/secretstorage/dhcrypto.py:15: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes
/usr/lib/python3/dist-packages/secretstorage/util.py:19: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes
You should consider upgrading via the '/usr/bin/python3 -m pip install --upgrade pip' command.


In [2]:
import nglview as nv # Для удобства переименовываю внутри скрипта модуль "nglview" на "nv".
import requests  
import json
# Импортирую необходимые модули.

Задание №1

In [4]:
my_query = {                    # Формирую заготовку для запроса.
    "query": {
        "type": "group",
        "logical_operator": "and",         
        "nodes": []
    },
    "return_type": "entry"
}

In [6]:
keyword_clause = {             # Добавляю в запрос о поиске ключевого слова "biotin".
    "type": "terminal",
    "service": "full_text",  # Означает поиск в любом текстовом поле записи.

    "parameters": {
        "value": "biotin"  # Указываю ключевое слово непосредственно.
    }
}

my_query["query"]["nodes"].append(keyword_clause) # Добавляю данный запрос в заготовку.

In [7]:
resolution_clause = {      # Устанавливаю запрос о требовании на разрешение не более 2.7 ангстрем. 
    "type": "terminal",
    "service": "text",
    "parameters": {
        "value": 2.7,
        "attribute": "rcsb_entry_info.resolution_combined",
        "operator": "less_or_equal"
    }
}

my_query["query"]["nodes"].append(resolution_clause)

In [8]:
has_ligand_clause = {      # Делаю запрос на количество лигандов, большее или равное единице. 
    "type": "terminal",
    "service": "text",
    "parameters": {
        "attribute": "rcsb_entry_info.nonpolymer_entity_count",
        "value": 0,
        "operator": "greater"
    }
}

my_query["query"]["nodes"].append(has_ligand_clause)

In [9]:
date_range_clause = {     # Оформляю запрос на соответствующий промежуток времени публикации. 
    "type": "terminal",
    "service": "text",
    "parameters": {
        "attribute": "rcsb_accession_info.initial_release_date",
        "value": {
            "from": "2010-01-01", 
            "to": "2015-01-01",
        },
        "operator": "range"
    }
}

my_query["query"]["nodes"].append(date_range_clause)

In [10]:
rcsb = 'https://search.rcsb.org/rcsbsearch/v1/query'   # Отправляю запрос на сервер RCSB.
json_query = json.dumps(my_query)
search = requests.post(f'{rcsb}', data=json_query) 

In [11]:
search # Проверяю, прошло ли всё хорошо.

<Response [200]>

In [12]:
search_result = search.json() #Распаковываю ответ сервера в словарь.
search_result

{'query_id': 'ad6d83e9-3622-4831-bed6-582767162b67',
 'result_type': 'entry',
 'total_count': 331,
 'result_set': [{'identifier': '4EKV',
   'score': 0.9966230893003007,
   'services': [{'service_type': 'full_text',
     'nodes': [{'node_id': 17149,
       'original_score': 9.762563705444336,
       'norm_score': 0.9915577232507522},
      {'node_id': 27112,
       'original_score': 9.762563705444336,
       'norm_score': 0.9915577232507522}]},
    {'service_type': 'text',
     'nodes': [{'node_id': 23771, 'original_score': 1.0, 'norm_score': 1.0},
      {'node_id': 29822, 'original_score': 1.0, 'norm_score': 1.0},
      {'node_id': 12008, 'original_score': 1.0, 'norm_score': 1.0}]}]},
  {'identifier': '4DVE',
   'score': 0.9946985114881184,
   'services': [{'service_type': 'full_text',
     'nodes': [{'node_id': 17149,
       'original_score': 9.720697402954102,
       'norm_score': 0.9867462787202961},
      {'node_id': 27112,
       'original_score': 9.720697402954102,
       'norm_

In [13]:
best_hit = search_result["result_set"][0] # Определяю лучшую находку.
best_hit

{'identifier': '4EKV',
 'score': 0.9966230893003007,
 'services': [{'service_type': 'full_text',
   'nodes': [{'node_id': 17149,
     'original_score': 9.762563705444336,
     'norm_score': 0.9915577232507522},
    {'node_id': 27112,
     'original_score': 9.762563705444336,
     'norm_score': 0.9915577232507522}]},
  {'service_type': 'text',
   'nodes': [{'node_id': 23771, 'original_score': 1.0, 'norm_score': 1.0},
    {'node_id': 29822, 'original_score': 1.0, 'norm_score': 1.0},
    {'node_id': 12008, 'original_score': 1.0, 'norm_score': 1.0}]}]}

Таким образом, далее я буду работать с PDB идентификатором 4EKV

Задание №2

Публикация, найденная по выявленному идентификатору "4EKV" содержит информацию о белке стрептавидине, (в данном случае это "мутеин", то есть белок с видоизменённой аминокислотной последовательностью) способном к обратимому связыванию биотина и являющемся гомотетрамером (A4). Экспериментальные данные получины с помощью рентгеновской дифракции. Мутеин был сконструирован специально для того, чтобы уменьшить чрезвычайно высокое сродство к биотину стрептавидина дикого типа. Кинетические параметры связывания делают данный мутеин превосходным агентом сродства для очистки биотинилированных молекул.   

Задание №3

In [14]:
from ipywidgets import interact, fixed # Импортирую небходимые для меня функции из модуля "ipywidgets".

In [16]:
representations = [                                                          # Задаю список с типами изображения белка.
  'ball+stick',      # Шаростержневая модель.
  'backbone',        # Прямые линии, соединяющие С-альфа атомы.
  'cartoon',         # Условное отображение вторичной структуры.
  'helixorient',     # Упрощенное отображение. 
  'hyperball',       # Сглаженная шаростержневая модель.
  'licorice',        # Стержневая модель (без шаров).
  'line',            # Очень тонкая стержневая модель.
  'point',           # Атомы в виде плоских точек.
  'ribbon',          # Отображение остова в виде ленты.
  'rocket',          # Отображение альфа-спиралей как цилиндров.
  'rope',            # Отображение остова в виде колбасы.
  'spacefill',       # Атомы в виде шаров соотв. Ван-дер-Ваальсова радиуса.
  'surface',         # Поверхность.
  'trace',           # Сглаженная линия, соединяющая С-альфа атомы.
  'tube'             # Более сдержанный rope.
]

In [17]:
colors = [                                                                 # Добавляю список с цветовыми схемами.
  'random',
  'uniform',
  'atomindex',      # От синего к красному с ростом номера атома.
  'residueindex',   # От синего к красному с ростом номера остатка.
  'chainindex',     # Каждой цепи свой цвет.
  'sstruc',         # Стандартные цвета для типа вторичной структуры.
  'element',        # Стандартные цвета для химических элементов.
  'resname',        # Свой цвет каждому из 20 остатков.
  'bfactor',        # Чем темнее, тем подвижнее.
  'hydrophobicity', # Чем темнее, тем гидрофобнее.
]

In [23]:
my_examples = {         # Создаю описания трёхмерных структур.
    'Rep_2': {
        'description': '''
Белок в виде cartoon, покраска от N к C концу
Боковые радикалы покрашены в светло-серый, показаны линиями
Боковые радикалы заряженных аминокислот показаны в стержневой модели
Лиганды показаны в шаростержневой модели, покрашены по элементам, углерод покрашен в любой цвет, кроме стандартного
''',
        'representations': [
            {
                'type': 'cartoon',                      
                'params': {
                    'sele': 'protein',              
                    'color': 'residueindex'
                 }
            },
            {
                'type': 'line',
                'params': {
                    'sele': 'sidechainAttached',                 
                    'color': 'LightGray'  
                 }
            },
            {
                'type': 'licorice',                      
                'params': {
                    'sele': 'sidechainAttached and charged',   
                 }
            },
            {
                'type': 'ball+stick',                      
                'params': {
                    'sele': 'ligand',               
                    'color': 'element'  
                }
            },
            {
                'type': 'ball+stick',
                'params': {
                    'sele': 'ligand AND _C',
                    'color': 'DarkViolet',
                }
            },
    ],
},
    'Rep_4': {
        'description': '''
Белок в виде cartoon, покраска по типу вторичной структуры
Боковые радикалы покрашены по элементу, показаны линиями
Боковые радикалы ароматических аминокислот показаны в стержневой модели
Лиганды показаны в виде Ван-дер-Ваальсовых сфер, покрашены по гидрофобности
''',
    'representations': [
        {
            'type': 'cartoon',
            'params':
            {
                'sele': 'protein',
                'color': 'sstruc'
            }
        },
        {
            'type': 'line',
            'params':
            {
               'sele': 'sidechainAttached',
                'color': 'element'
            }
        },
        {
            'type': 'licorice',
            'params':
            {
                'sele': 'sidechainAttached and aromatic',
                'color': 'resname'
            }
        },
        {
            'type': 'spacefill',
            'params':
            {
                'sele': 'ligand',
                'color': 'hydrophobicity'

            }
        }
    ],
},
    'Rep_8': {
        'description': '''
Поверхность белка покрашена в белый, с непрозрачностью 0.1
Белок в виде cartoon темно-серого цвета
Боковые радикалы в стержневой модели, покрашены по гидрофобности
Лиганды в виде Ван-дер-Ваальсовых сфер, покрашены по элементам
''',
        'representations': [
            {
                'type': 'surface',                      
                'params': {
                    'sele': 'protein',               
                    'color': 'white',  
                    'opacity': 0.1
                 }
            },
            {
                'type': 'cartoon',                      
                'params': {
                    'sele': 'protein',                     
                    'color': 'darkslategray'  
                 }
            },
            {
                'type': 'licorice',                      
                'params': {
                    'sele': 'sidechainAttached',                     
                    'color': 'hydrophobicity'  
                 }
            },
            {
                'type': 'spacefill',
                'params': {
                    'sele': 'ligand',                     
                    'color': 'element'  
                 }
            },
        ],
    },
}            

In [25]:
def show_examples(view, example_name):
    view.clear()
    example = my_examples[example_name]
    print(example['description'])
    view.set_representations(example['representations'])
    view.center()

view = nv.show_pdbid("4ekv", default_representation=False)
interact(show_examples, view=fixed(view), example_name=list(my_examples.keys()))
view

interactive(children=(Dropdown(description='example_name', options=('Rep_2', 'Rep_4', 'Rep_8'), value='Rep_2')…

NGLWidget()